In [1]:
import pandas as pd
import numpy as np
import re
from sklearn.impute import SimpleImputer
fdp = pd.read_csv('fdp-beta-regional-historical.csv')
fdp.head()

Variable  Year     ABARES region   Value   RSE
0  AI stud fees and herd testing ($)  1990  NSW Central West    90.0  68.0
1            Accounting services ($)  1990  NSW Central West  2320.0  19.0
2              Advisory services ($)  1990  NSW Central West   120.0  80.0
3         Age of owner manager (yrs)  1990  NSW Central West    57.0   5.0
4                Age of spouse (yrs)  1990  NSW Central West    51.0   4.0

In [2]:
print(pd.unique(fdp['ABARES region']))

['NSW Central West' 'NSW Coastal' 'NSW Far West'
 'NSW North West Slopes and Plains' 'NSW Riverina'
 'NSW Tablelands (Northern Central and Southern)'
 'NT Alice Springs Districts' 'QLD Cape York and the Gulf'
 'QLD Central North' 'QLD Charleville - Longreach'
 'QLD Eastern Darling Downs' 'QLD Northern Coastal - Mackay to Cairns'
 'QLD Southern Coastal - Curtis to Moreton' 'QLD West and South West'
 'QLD Western Downs and Central Highlands' 'SA Eyre Peninsula'
 'SA Murray Lands and Yorke Peninsula' 'SA Northern Pastoral'
 'SA South East' 'TAS Tasmania' 'VIC Central North' 'VIC Mallee'
 'VIC Southern and Eastern Victoria' 'VIC Wimmera'
 'WA Central and Southern Wheat Belt' 'WA Northern and Eastern Wheat Belt'
 'WA Pilbara and Central Pastoral' 'WA South West Coastal'
 'WA The Kimberley' 'NT Barkly Tablelands' 'NT Top End Darwin'
 'NT Victoria River District - Katherine']


In [3]:
pivoted = pd.pivot_table(fdp, index=['ABARES region', 'Year'], columns='Variable', values='Value')

pivoted


Variable               AI stud fees and herd testing ($)  \
ABARES region    Year                                      
NSW Central West 1990                               90.0   
                 1991                              310.0   
                 1992                               90.0   
                 1993                              150.0   
                 1994                               90.0   
...                                                  ...   
WA The Kimberley 2018                             6150.0   
                 2019                                0.0   
                 2020                                0.0   
                 2021                                0.0   
                 2022                                0.0   

Variable               Accounting services ($)  Advisory services ($)  \
ABARES region    Year                                                   
NSW Central West 1990                   2320.0                  120.0   
                 1991                   2290.0                  210.0   
                 1992                   2790.0                  730.0   
                 1993                   2180.0                  280.0   
                 1994                   2430.0                  190.0   
...                                        ...                    ...   
WA The Kimberley 2018                  11550.0                14640.0   
                 2019                   8290.0                14920.0   
                 2020                   4410.0                29650.0   
                 2021                   7300.0                32670.0   
                 2022                   4900.0                    0.0   

Variable               Age of owner manager (yrs)  Age of spouse (yrs)  \
ABARES region    Year                                                    
NSW Central West 1990                        57.0                 51.0   
                 1991                        54.0                 51.0   
                 1992                        52.0                 49.0   
                 1993                        54.0                 50.0   
                 1994                        53.0                 49.0   
...                                           ...                  ...   
WA The Kimberley 2018                         NaN                  NaN   
                 2019                         NaN                  NaN   
                 2020                         NaN                  NaN   
                 2021                         NaN                  NaN   
                 2022                         NaN                  NaN   

Variable               Agistment ($)  Area operated at 30 June (ha)  \
ABARES region    Year                                                 
NSW Central West 1990          290.0                         1132.0   
                 1991          370.0                         1054.0   
                 1992          250.0                         1061.0   
                 1993          430.0                         1018.0   
                 1994          310.0                         1065.0   
...                              ...                            ...   
WA The Kimberley 2018        42280.0                       488457.0   
                 2019            0.0                       615790.0   
                 2020            0.0                       451519.0   
                 2021            0.0                       520690.0   
                 2022            0.0                       311732.0   

Variable               Barley area sown (ha)  Barley produced (t)  \
ABARES region    Year                                               
NSW Central West 1990                   21.0                 37.0   
                 1991                   14.0                 24.0   
                 1992                   20.0                 34.0   
                 1993                

In [4]:
pivot = pd.pivot_table(fdp, index=['Year', 'ABARES region'], columns='Variable', values='Value')
pivot.reset_index(inplace=True)
pivot


Variable  Year                       ABARES region  \
0         1990                    NSW Central West   
1         1990                         NSW Coastal   
2         1990                        NSW Far West   
3         1990    NSW North West Slopes and Plains   
4         1990                        NSW Riverina   
...        ...                                 ...   
1045      2022  WA Central and Southern Wheat Belt   
1046      2022  WA Northern and Eastern Wheat Belt   
1047      2022     WA Pilbara and Central Pastoral   
1048      2022               WA South West Coastal   
1049      2022                    WA The Kimberley   

Variable  AI stud fees and herd testing ($)  Accounting services ($)  \
0                                      90.0                   2320.0   
1                                      20.0                   1070.0   
2                                    1510.0                   5850.0   
3                                      70.0                   3030.0   
4                                     150.0                   2550.0   
...                                     ...                      ...   
1045                                  100.0                   8200.0   
1046                                    0.0                  10800.0   
1047                                    0.0                   4100.0   
1048                                  900.0                   6800.0   
1049                                    0.0                   4900.0   

Variable  Advisory services ($)  Age of owner manager (yrs)  \
0                         120.0                        57.0   
1                         350.0                        58.0   
2                         180.0                        57.0   
3                         320.0                        55.0   
4                         210.0                        50.0   
...                         ...                         ...   
1045                     8100.0                        61.0   
1046                     5500.0                        66.0   
1047                     4800.0                        60.0   
1048                      800.0                        61.0   
1049                        0.0                         NaN   

Variable  Age of spouse (yrs)  Agistment ($)  Area operated at 30 June (ha)  \
0                        51.0          290.0                         1132.0   
1                        52.0         3300.0                          492.0   
2                        55.0          340.0                        24478.0   
3                        50.0         2260.0                         1762.0   
4                        50.0         7040.0                         1222.0   
...                       ...            ...                            ...   
1045                     57.0          500.0                         2987.0   
1046                     59.0          400.0                         5077.0   
1047                     56.0         5400.0                       320352.0   
1048                     58.0          400.0                          784.0   
1049                      NaN            0.0                       311732.0   

Variable  Barley area sown (ha)  ...  Wages for hired labor ($)  \
0                          21.0  ...                    11910.0   
1                           0.0  ...                     3640.0   
2                           3.0  ...                    19320.0   
3                          36.0  ...                    12950.0   
4                          20.0  ...                     9810.0   
...                         ...  ...                        ...   
1045                      378.0  ...                    81600.0   
1046                      462.0  ...                    39800.0   
1047                        0.0  ...                   133700.0   
1048                       46.0  ...                    16600.0   
1049                        0.0  ...       

In [5]:
import geopandas as gpd

geojson = gpd.read_file("states.geojson")
geojson

STATE_CODE STATE_NAME                                           geometry
0          1        NSW  MULTIPOLYGON (((159.10542 -31.56399, 159.09775...
1          2        VIC  MULTIPOLYGON (((145.13189 -38.39069, 145.12993...
2          3        QLD  MULTIPOLYGON (((141.66351 -15.00396, 141.59026...
3          4         SA  MULTIPOLYGON (((138.50022 -34.84357, 138.51080...
4          5         WA  MULTIPOLYGON (((113.39418 -26.39303, 113.38230...
5          6        TAS  MULTIPOLYGON (((148.48189 -40.43493, 148.47286...
6          7         NT  MULTIPOLYGON (((130.51789 -12.73105, 130.51753...
7          8        ACT  POLYGON ((149.39928 -35.31918, 149.35213 -35.3...

In [6]:
pivot['State'] = pivot['ABARES region'].str.slice(stop=3)
pivot

Variable  Year                       ABARES region  \
0         1990                    NSW Central West   
1         1990                         NSW Coastal   
2         1990                        NSW Far West   
3         1990    NSW North West Slopes and Plains   
4         1990                        NSW Riverina   
...        ...                                 ...   
1045      2022  WA Central and Southern Wheat Belt   
1046      2022  WA Northern and Eastern Wheat Belt   
1047      2022     WA Pilbara and Central Pastoral   
1048      2022               WA South West Coastal   
1049      2022                    WA The Kimberley   

Variable  AI stud fees and herd testing ($)  Accounting services ($)  \
0                                      90.0                   2320.0   
1                                      20.0                   1070.0   
2                                    1510.0                   5850.0   
3                                      70.0                   3030.0   
4                                     150.0                   2550.0   
...                                     ...                      ...   
1045                                  100.0                   8200.0   
1046                                    0.0                  10800.0   
1047                                    0.0                   4100.0   
1048                                  900.0                   6800.0   
1049                                    0.0                   4900.0   

Variable  Advisory services ($)  Age of owner manager (yrs)  \
0                         120.0                        57.0   
1                         350.0                        58.0   
2                         180.0                        57.0   
3                         320.0                        55.0   
4                         210.0                        50.0   
...                         ...                         ...   
1045                     8100.0                        61.0   
1046                     5500.0                        66.0   
1047                     4800.0                        60.0   
1048                      800.0                        61.0   
1049                        0.0                         NaN   

Variable  Age of spouse (yrs)  Agistment ($)  Area operated at 30 June (ha)  \
0                        51.0          290.0                         1132.0   
1                        52.0         3300.0                          492.0   
2                        55.0          340.0                        24478.0   
3                        50.0         2260.0                         1762.0   
4                        50.0         7040.0                         1222.0   
...                       ...            ...                            ...   
1045                     57.0          500.0                         2987.0   
1046                     59.0          400.0                         5077.0   
1047                     56.0         5400.0                       320352.0   
1048                     58.0          400.0                          784.0   
1049                      NaN            0.0                       311732.0   

Variable  Barley area sown (ha)  ...  Water charges ($)  \
0                          21.0  ...             1290.0   
1                           0.0  ...               70.0   
2                           3.0  ...              350.0   
3                          36.0  ...              540.0   
4                          20.0  ...             8770.0   
...                         ...  ...                ...   
1045                      378.0  ...             2400.0   
1046                      462.0  ...             2400.0   
1047                        0.0  ...              400.0   
1048                       46.0  ...                0.0   
1049                        0.0  ...                0.0   

Variable  Wethers at 30 June (no.)  Wheat area sown (ha)  Wheat produce

In [7]:
mean_by_state = pivot.groupby(['Year', 'State']).mean().round(1)
mean_by_state

Variable    AI stud fees and herd testing ($)  Accounting services ($)  \
Year State                                                               
1990 NSW                                356.7                   2950.0   
     NT                                   0.0                  16000.0   
     QLD                               1946.2                   3851.2   
     SA                                 212.5                   3220.0   
     TAS                               1260.0                   2890.0   
...                                       ...                      ...   
2022 QLD                                587.5                   5325.0   
     SA                                  75.0                   5950.0   
     TAS                               2700.0                   5500.0   
     VIC                                350.0                   4400.0   
     WA                                 200.0                   6960.0   

Variable    Advisory services ($)  Age of owner manager (yrs)  \
Year State                                                      
1990 NSW                    205.0                        55.7   
     NT                    3020.0                        52.0   
     QLD                     47.5                        53.2   
     SA                      45.0                        49.8   
     TAS                    160.0                        52.0   
...                           ...                         ...   
2022 QLD                   1050.0                        64.4   
     SA                    1475.0                        61.0   
     TAS                   1400.0                        64.0   
     VIC                   2125.0                        63.8   
     WA                    3840.0                        62.0   

Variable    Age of spouse (yrs)  Agistment ($)  Area operated at 30 June (ha)  \
Year State                                                                      
1990 NSW                   52.0         2321.7                         4967.0   
     NT                    47.0        17230.0                       328628.0   
     QLD                   48.0         5456.2                        35216.9   
     SA                    47.8          410.0                        22888.2   
     TAS                   51.0           30.0                          775.0   
...                         ...            ...                            ...   
2022 QLD                   61.0        12437.5                        39309.4   
     SA                    57.2         1075.0                        36880.2   
     TAS                   62.0         2900.0                          842.0   
     VIC                   61.2          800.0                         1133.8   
     WA                    57.5         1340.0                       128186.4   

Variable    Barley area sown (ha)  Barley produced (t)  Barley receipts ($)  \
Year State                                                                    
1990 NSW                     13.5                 24.2               8018.3   
     NT                       0.0                  0.0                  0.0   
     QLD                      5.5                  7.0               1937.5   
     SA                      66.8                143.5              43192.5   
     TAS                      4.0                  8.0               3170.0   
...                           ...                  ...                  ...   
2022 QLD                     11.4                 37.6              12050.0   
     SA                     122.8                256.5              72750.0   
     TAS                      3.0                 17.0               4300.0   
     VIC                    168.2                419.5             121000.0   
     WA                     177.2                569.6             114400.0   

Variable    ...  Wages for hired labor ($)  Water charges ($)  \
Year State  ...                             

In [8]:
state_mean = mean_by_state.reset_index()
# state_mean = state_mean.merge(geojson, left_on=mean_by_state.index.get_level_values('STATE_NAME'), right_on='STATE_NAME')

In [9]:
state_mean


Variable  Year State  AI stud fees and herd testing ($)  \
0         1990   NSW                              356.7   
1         1990   NT                                 0.0   
2         1990   QLD                             1946.2   
3         1990   SA                               212.5   
4         1990   TAS                             1260.0   
..         ...   ...                                ...   
226       2022   QLD                              587.5   
227       2022   SA                                75.0   
228       2022   TAS                             2700.0   
229       2022   VIC                              350.0   
230       2022   WA                               200.0   

Variable  Accounting services ($)  Advisory services ($)  \
0                          2950.0                  205.0   
1                         16000.0                 3020.0   
2                          3851.2                   47.5   
3                          3220.0                   45.0   
4                          2890.0                  160.0   
..                            ...                    ...   
226                        5325.0                 1050.0   
227                        5950.0                 1475.0   
228                        5500.0                 1400.0   
229                        4400.0                 2125.0   
230                        6960.0                 3840.0   

Variable  Age of owner manager (yrs)  Age of spouse (yrs)  Agistment ($)  \
0                               55.7                 52.0         2321.7   
1                               52.0                 47.0        17230.0   
2                               53.2                 48.0         5456.2   
3                               49.8                 47.8          410.0   
4                               52.0                 51.0           30.0   
..                               ...                  ...            ...   
226                             64.4                 61.0        12437.5   
227                             61.0                 57.2         1075.0   
228                             64.0                 62.0         2900.0   
229                             63.8                 61.2          800.0   
230                             62.0                 57.5         1340.0   

Variable  Area operated at 30 June (ha)  Barley area sown (ha)  ...  \
0                                4967.0                   13.5  ...   
1                              328628.0                    0.0  ...   
2                               35216.9                    5.5  ...   
3                               22888.2                   66.8  ...   
4                                 775.0                    4.0  ...   
..                                  ...                    ...  ...   
226                             39309.4                   11.4  ...   
227                             36880.2                  122.8  ...   
228                               842.0                    3.0  ...   
229                              1133.8                  168.2  ...   
230                            128186.4                  177.2  ...   

Variable  Wages for hired labor ($)  Water charges ($)  \
0                           11935.0             1861.7   
1                          190350.0                0.0   
2                           27771.2              855.0   
3                           18837.5              307.5   
4                           21990.0              260.0   
..                              ...                ...   
226                         61350.0              400.0   
227                         42625.0             3225.0   
228                         26600.0             3900.0   
229                         16000.0             5075.0   
230                        206800.0             1040.0   

Variable  Wethers at 30 June (no.)  Wheat area sown (ha)  Wheat produced (t)  \
0                          

In [10]:
geodata = state_mean.merge(geojson, left_on='State', right_on = 'STATE_NAME')

In [11]:
geodata
print(type(geodata))

<class 'pandas.core.frame.DataFrame'>


In [12]:
import plotly.express as px
geodata['geometry'] = geodata['geometry'].apply(lambda x: str(x))
fig = px.choropleth(geodata, 
                    geojson=geodata.geometry, 
                    locations=geodata.State, 
                    color='Farm business profit ($)',
                    color_continuous_scale='Viridis',
                    featureidkey='properties.STATE_NAME',
                    projection="mercator"
                   )
fig.update_geos(fitbounds="locations", visible=False)
fig.show()

In [13]:
imputer = SimpleImputer(missing_values=np.NaN, strategy = 'mean')
barley = fdp.loc[(fdp['Variable']=='Barley produced (t)') & (fdp['ABARES region'].str.contains('NSW'))]

barley_imputed = imputer.fit_transform(barley['Value'].values.reshape(-1,1))[:,0]
barley.loc[:, 'Imputed value'] = barley_imputed

display(barley)

hours_worked = fdp.loc[(fdp['Variable']=='Hours worked on farm - total (hrsperwk)') & (fdp['ABARES region'].str.contains('NSW'))]
mimputer = SimpleImputer(missing_values=np.NaN, strategy = 'mean')
hours_imputed = mimputer.fit_transform(hours_worked['Value'].values.reshape(-1,1))[:,0]
hours_worked.loc[:, 'Imputed value'] = hours_imputed
hours_worked['Imputed value'] = hours_worked['Imputed value'].round(1)
display(hours_worked)

/var/folders/ly/fm0kkb6x1b91l8mnvhcy7kg00000gn/T/ipykernel_7794/3771514738.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Variable  Year  \
8       Barley produced (t)  1990   
144     Barley produced (t)  1990   
280     Barley produced (t)  1990   
416     Barley produced (t)  1990   
552     Barley produced (t)  1990   
...                     ...   ...   
138592  Barley produced (t)  2022   
138728  Barley produced (t)  2022   
138864  Barley produced (t)  2022   
139000  Barley produced (t)  2022   
139136  Barley produced (t)  2022   

                                         ABARES region  Value    RSE  \
8                                     NSW Central West   37.0   49.0   
144                                        NSW Coastal    0.0    NaN   
280                                       NSW Far West    5.0  157.0   
416                   NSW North West Slopes and Plains   66.0   39.0   
552                                       NSW Riverina   35.0   34.0   
...                                                ...    ...    ...   
138592                                     NSW Coastal    1.0  173.0   
138728                                    NSW Far West  114.0   38.0   
138864                NSW North West Slopes and Plains  570.0   20.0   
139000                                    NSW Riverina  353.0   24.0   
139136  NSW Tablelands (Northern Central and Southern)    9.0   74.0   

        Imputed value  
8                37.0  
144               0.0  
280               5.0  
416              66.0  
552              35.0  
...               ...  
138592            1.0  
138728          114.0  
138864          570.0  
139000          353.0  
139136            9.0  

[198 rows x 6 columns]

/var/folders/ly/fm0kkb6x1b91l8mnvhcy7kg00000gn/T/ipykernel_7794/3771514738.py:12: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/ly/fm0kkb6x1b91l8mnvhcy7kg00000gn/T/ipykernel_7794/3771514738.py:13: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Variable  Year  \
54      Hours worked on farm - total (hrsperwk)  1990   
190     Hours worked on farm - total (hrsperwk)  1990   
326     Hours worked on farm - total (hrsperwk)  1990   
462     Hours worked on farm - total (hrsperwk)  1990   
598     Hours worked on farm - total (hrsperwk)  1990   
...                                         ...   ...   
138638  Hours worked on farm - total (hrsperwk)  2022   
138774  Hours worked on farm - total (hrsperwk)  2022   
138910  Hours worked on farm - total (hrsperwk)  2022   
139046  Hours worked on farm - total (hrsperwk)  2022   
139182  Hours worked on farm - total (hrsperwk)  2022   

                                         ABARES region  Value   RSE  \
54                                    NSW Central West    NaN   NaN   
190                                        NSW Coastal    NaN   NaN   
326                                       NSW Far West    NaN   NaN   
462                   NSW North West Slopes and Plains    NaN   NaN   
598                                       NSW Riverina    NaN   NaN   
...                                                ...    ...   ...   
138638                                     NSW Coastal   70.0  13.0   
138774                                    NSW Far West  135.0  11.0   
138910                NSW North West Slopes and Plains  113.0   7.0   
139046                                    NSW Riverina   97.0   6.0   
139182  NSW Tablelands (Northern Central and Southern)   79.0   7.0   

        Imputed value  
54               91.5  
190              91.5  
326              91.5  
462              91.5  
598              91.5  
...               ...  
138638           70.0  
138774          135.0  
138910          113.0  
139046           97.0  
139182           79.0  

[198 rows x 6 columns]

In [14]:
hoursvsbarley = barley.merge(hours_worked, how= "inner", left_on=['Year', 'ABARES region'], right_on=['Year', 'ABARES region'])
hoursvsbarley

Variable_x  Year  \
0    Barley produced (t)  1990   
1    Barley produced (t)  1990   
2    Barley produced (t)  1990   
3    Barley produced (t)  1990   
4    Barley produced (t)  1990   
..                   ...   ...   
193  Barley produced (t)  2022   
194  Barley produced (t)  2022   
195  Barley produced (t)  2022   
196  Barley produced (t)  2022   
197  Barley produced (t)  2022   

                                      ABARES region  Value_x  RSE_x  \
0                                  NSW Central West     37.0   49.0   
1                                       NSW Coastal      0.0    NaN   
2                                      NSW Far West      5.0  157.0   
3                  NSW North West Slopes and Plains     66.0   39.0   
4                                      NSW Riverina     35.0   34.0   
..                                              ...      ...    ...   
193                                     NSW Coastal      1.0  173.0   
194                                    NSW Far West    114.0   38.0   
195                NSW North West Slopes and Plains    570.0   20.0   
196                                    NSW Riverina    353.0   24.0   
197  NSW Tablelands (Northern Central and Southern)      9.0   74.0   

     Imputed value_x                               Variable_y  Value_y  RSE_y  \
0               37.0  Hours worked on farm - total (hrsperwk)      NaN    NaN   
1                0.0  Hours worked on farm - total (hrsperwk)      NaN    NaN   
2                5.0  Hours worked on farm - total (hrsperwk)      NaN    NaN   
3               66.0  Hours worked on farm - total (hrsperwk)      NaN    NaN   
4               35.0  Hours worked on farm - total (hrsperwk)      NaN    NaN   
..               ...                                      ...      ...    ...   
193              1.0  Hours worked on farm - total (hrsperwk)     70.0   13.0   
194            114.0  Hours worked on farm - total (hrsperwk)    135.0   11.0   
195            570.0  Hours worked on farm - total (hrsperwk)    113.0    7.0   
196            353.0  Hours worked on farm - total (hrsperwk)     97.0    6.0   
197              9.0  Hours worked on farm - total (hrsperwk)     79.0    7.0   

     Imputed value_y  
0               91.5  
1               91.5  
2               91.5  
3               91.5  
4               91.5  
..               ...  
193             70.0  
194            135.0  
195            113.0  
196             97.0  
197             79.0  

[198 rows x 10 columns]

In [15]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import dash
import dash_core_components as dcc
import dash_html_components as html
from dash.dependencies import Input, Output

/var/folders/ly/fm0kkb6x1b91l8mnvhcy7kg00000gn/T/ipykernel_7794/2358614273.py:6: UserWarning:


The dash_core_components package is deprecated. Please replace
`import dash_core_components as dcc` with `from dash import dcc`

/var/folders/ly/fm0kkb6x1b91l8mnvhcy7kg00000gn/T/ipykernel_7794/2358614273.py:7: UserWarning:


The dash_html_components package is deprecated. Please replace
`import dash_html_components as html` with `from dash import html`



In [16]:
print(geodata.geometry)

0      MULTIPOLYGON (((159.10542 -31.563994, 159.0977...
1      MULTIPOLYGON (((159.10542 -31.563994, 159.0977...
2      MULTIPOLYGON (((159.10542 -31.563994, 159.0977...
3      MULTIPOLYGON (((159.10542 -31.563994, 159.0977...
4      MULTIPOLYGON (((159.10542 -31.563994, 159.0977...
                             ...                        
127    MULTIPOLYGON (((145.131889 -38.390694, 145.129...
128    MULTIPOLYGON (((145.131889 -38.390694, 145.129...
129    MULTIPOLYGON (((145.131889 -38.390694, 145.129...
130    MULTIPOLYGON (((145.131889 -38.390694, 145.129...
131    MULTIPOLYGON (((145.131889 -38.390694, 145.129...
Name: geometry, Length: 132, dtype: object


In [17]:
anti = pivoted.dropna()

In [18]:
print(type(barley['ABARES region'].unique().tolist()))


<class 'list'>


In [19]:
import requests

url = "https://api.mapbox.com/tokens/v2/tinshen?access_token=pk.eyJ1IjoidGluc2hlbiIsImEiOiJjbGhocjhpd3AwMG5yM2VzNXZqNXU5bjczIn0.DTGmjolI-YUV9Gxk6-bcFQ"
response = requests.get(url)
api_token = response.text



In [20]:
import numpy as np
from scipy import stats
import matplotlib.pyplot as plt
import plotly.graph_objs as go

wool_produced = np.array(geodata['Wool produced (kg)'])
wheat_sold = np.array(geodata['Wheat sold (t)'])
slope, intercept, r_value, p_value, std_err = stats.linregress(wool_produced, wheat_sold)
fig1 = go.Figure()
x = np.linspace(min(wool_produced), max(wool_produced), 100)
y = slope * x + intercept
fig1 = px.scatter(x= wool_produced, y= wheat_sold, labels=dict(x = 'Wool produced (kg)',y = 'Wheat sold (t)' ))
fig1 = fig1.add_trace(go.Scatter(x=x, y=y,
                    mode='lines'
                    ))
fig1.show()

In [21]:
from dash import Dash, html, dcc, callback, Output, Input
import plotly.express as px
import pandas as pd

options = barley['ABARES region'].unique().tolist()

app = Dash(__name__, external_stylesheets=["./style.css"])

app.layout = html.Div(
    [
        html.Div(
            [
                html.H1(
                    children="Progression of Barley yield from 1990 to 2022",
                    style={
                        "textAlign": "center",
                        "font-family": "Tahoma",
                        "color": "#ffffff",
                    },
                ),
                dcc.Dropdown(
                    options=options,
                    value="NSW Central West",
                    id="dropdown-selection",
                ),
                dcc.Graph(id="years-vs-barley",
                style={"padding" : "1%"}),
            ],
            id="pvb-container",
        ),
        html.Div(
            [
                html.H1(
                children=[ "Effects of amount of work on ", html.Span("corn", style={"color": "#ffe6a6"}), " production" ],
                style={"textAlign": "center", "font-family": "Tahoma", "color": "#ffffff"},
                className="Title"
                ),
                dcc.Dropdown(
                    options=["QL", "TAS", "WA", "VIC", "SA", "NSW"],
                    value="NSW",
                    id="state-dropdown",
                    style= {'font-family': 'Tahoma',
                    'font-size': '16px',
                    'background-color': '#ffffff',
                    'color': '#000000',
                    'border': '1px solid #000000'

                    }
                ),
                dcc.Graph(
                    id="work-vs-yield",
                    style={"padding" : "1%"},
                ),
            ],
            id="eoc-container",
            style={"color" : "rgb(15, 97, 88)"}
        ),
        html.Div(
            [
                html.H1(
                children= "Correlation and its best fit",
                style={"textAlign": "center", "font-family": "Tahoma", "color": "#ffffff"},
                className="Title"
                ),
                html.Div(children=[
                    html.Label('Checkboxes_x'),
                    dcc.Checklist(['Wool produced (kg)', 'Wheat sold (t)', 'Barley produced (t)', 'Sheep receipts ($)'],
                      ['Wool produced (kg)'], id="checkbox-x", style = {"color": "#ffffff",  "font-family": "Tahoma", "font-size": "16px"}
                      )
                      ],
                      ),
                html.Div(children=[
                    html.Label('Checkboxes_y'),
                    dcc.Checklist(['Wool produced (kg)', 'Wheat sold (t)', 'Barley produced (t)', 'Sheep receipts ($)'],
                      ['Wheat sold (t)'], id = 'checkbox-y', style = {"color": "#ffffff",  "font-family": "Tahoma", "font-size": "16px"}
                      )
                      ],
                      ),
                dcc.Graph(
                    id="corr-var",
                    style={"padding" : "1%"},
                ),
            ],
            id= "bf-corr",
            style = {"color" : "rgb(15, 97, 88)"}

        )
    ],
    id="overall-container",
    style={"padding": "10%", "backgroundColor": "rgb(15, 97, 88)"},
)


@callback(
    Output("years-vs-barley", "figure"),
    Input("dropdown-selection", "value"),
)
def update_graph(value):
    dff = barley.loc[barley["ABARES region"] == value]
    return px.line(dff, x="Year", y="Imputed value")


@callback(
    Output("work-vs-yield", "figure"),
    Input("state-dropdown", "value"),
)
def update_graph2(value):
    filtered = anti[
        anti.index.get_level_values("ABARES region").str.contains(value)
    ]
    return px.scatter(
        filtered,
        "Hours worked on farm - total (hrsperwk)",
        "Barley produced (t)",
        color=filtered.index.get_level_values("ABARES region"),
        size="Area operated at 30 June (ha)",
    )

@callback(
    Output("corr-var", "figure"),
    inputs = {
        "all_inputs": {
            "checkbox-x": Input("checkbox-x",  "value"),
            "checkbox-y": Input("checkbox-y", "value")
        }
    }
)

def update_graph():
    return 


if __name__ == "__main__":
    app.run(debug=False, port=8054)


Dash is running on http://127.0.0.1:8054/

 * Serving Flask app '__main__'
 * Debug mode: off


 * Running on http://127.0.0.1:8054
Press CTRL+C to quit
127.0.0.1 - - [11/May/2023 12:46:07] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [11/May/2023 12:46:07] "GET /style.css HTTP/1.1" 200 -
127.0.0.1 - - [11/May/2023 12:46:07] "GET /_dash-layout HTTP/1.1" 200 -
127.0.0.1 - - [11/May/2023 12:46:07] "GET /_dash-dependencies HTTP/1.1" 200 -
127.0.0.1 - - [11/May/2023 12:46:07] "GET /_favicon.ico?v=2.8.1 HTTP/1.1" 200 -
127.0.0.1 - - [11/May/2023 12:46:07] "GET /_dash-component-suites/dash/dcc/async-dropdown.js HTTP/1.1" 304 -
127.0.0.1 - - [11/May/2023 12:46:07] "GET /_dash-component-suites/dash/dcc/async-graph.js HTTP/1.1" 304 -
127.0.0.1 - - [11/May/2023 12:46:07] "GET /_dash-component-suites/dash/dcc/async-plotlyjs.js HTTP/1.1" 304 -
127.0.0.1 - - [11/May/2023 12:46:07] "POST /_dash-update-component HTTP/1.1" 200 -
127.0.0.1 - - [11/May/2023 12:46:07] "POST /_dash-update-component HTTP/1.1" 200 -
